In [1]:
conda install -c conda-forge ipywidgets

Solving environment: ...working... done

# All requested packages already installed.


Note: you may need to restart the kernel to use updated packages.


In [2]:
import pandas as pd
import folium as fo
import re
import bs4 
import requests 
import ipywidgets as widgets

In [3]:
def get_data():  
    headers = {"User-Agent":"Mozilla/5.0 (Windows NT 10.0; Win64; x64; rv:66.0) Gecko/20100101 Firefox/66.0", "Accept-Encoding":"gzip, deflate", "Accept":"text/html,application/xhtml+xml,application/xml;q=0.9,*/*;q=0.8", "DNT":"1","Connection":"close", "Upgrade-Insecure-Requests":"1"}

    pagina = requests.get('http://queimadas.dgi.inpe.br/queimadas/dados-abertos/')
    content = pagina.content
    soup = bs4.BeautifulSoup(content)

    lista_regiao_url = []
    lista_regiao = []
    
    for tr in soup.findAll('tr'):                        
        regiao_url = []        
        regiao_nome = []        
        for td in tr.findAll('td'):                        
            
            regiao_nome.append(td.get_text().strip())                                    
            for a in td.find_all('a'):                
                if (len(regiao_nome)==4):   #dados csv 48h                  
                    regiao_url.append(a.get('href'))                    
            
        lista_regiao_url.append([regiao_nome[0],regiao_url[0]])
        lista_regiao.append(regiao_nome[0])
        
    return lista_regiao_url,  lista_regiao
    
lista = get_data()

In [4]:
print('Selecione a regiao que deseja inspecionar os focos de incendio:')
ToggleButtons_regiao = widgets.ToggleButtons(
    options=lista[1],    
    value=lista[1][1],    
    disabled=False    
)

display(ToggleButtons_regiao)

Selecione a regiao que deseja inspecionar os focos de incendio:


ToggleButtons(index=1, options=('América do Sul', 'Brasil', 'Acre', 'Alagoas', 'Amapá', 'Amazonas', 'Bahia', '…

In [5]:
idx = lista[1].index(ToggleButtons_regiao.value)

In [6]:
print(idx)

1


In [7]:
url = 'http://queimadas.dgi.inpe.br' +  str(lista[0][idx][1])
print(url)

http://queimadas.dgi.inpe.br/queimadas/dados-abertos/download/?utm_campaign=dados-abertos&outputFormat=csv&utm_medium=landing-page&time=48h&utm_content=focos_brasil_48h&id=focos_brasil&utm_source=landing-page


In [8]:
CSV_URL = url
#'http://queimadas.dgi.inpe.br/queimadas/dados-abertos/download/?utm_campaign=dados-abertos&outputFormat=csv&utm_medium=landing-page&time=48h&utm_content=focos_brasil_48h&id=focos_brasil&utm_source=landing-page'

In [9]:
df = pd.read_csv(CSV_URL)

In [10]:
df.head()

FID  \
0  focos_brasil_ontem_hoje_ref.1edd7917-396d-3539...   
1  focos_brasil_ontem_hoje_ref.96e54dcf-8c5d-3a97...   
2  focos_brasil_ontem_hoje_ref.4d6581fd-392b-3bc9...   
3  focos_brasil_ontem_hoje_ref.af631f77-4648-3b79...   
4  focos_brasil_ontem_hoje_ref.7275bf53-ac36-3fde...   

                                     id  longitude  latitude  \
0  1edd7917-396d-3539-86c8-3d85aee9f39a    -67.480    -9.117   
1  96e54dcf-8c5d-3a97-b1d2-37fa886e2487    -67.513    -9.055   
2  4d6581fd-392b-3bc9-aa9d-ffe1b6ad004f    -64.141    -8.957   
3  af631f77-4648-3b79-89a7-58e5a2cb0b12    -68.768    -8.867   
4  7275bf53-ac36-3fde-8745-2ae8e1bb2104    -69.001   -10.620   

         data_hora_gmt  satelite     municipio    estado    pais  \
0  2020-09-20T18:35:00  AQUA_M-T  BOCA DO ACRE  AMAZONAS  Brasil   
1  2020-09-20T18:35:00  AQUA_M-T  BOCA DO ACRE  AMAZONAS  Brasil   
2  2020-09-20T18:35:00  AQUA_M-T   PORTO VELHO  RONDÔNIA  Brasil   
3  2020-09-20T18:35:00  AQUA_M-T  BOCA DO ACRE  AMAZONAS  Brasil   
4  2020-09-20T18:35:00  AQUA_M-T     BRASILÉIA      ACRE  Brasil   

   municipio_id  estado_id  pais_id  numero_dias_sem_chuva  precipitacao  \
0       1300706         13       33                    NaN           NaN   
1       1300706         13       33                    NaN           NaN   
2       1100205         11       33                    NaN           NaN   
3       1300706         13       33                    NaN           NaN   
4       1200104         12       33                    NaN           NaN   

   risco_fogo     bioma                    geom  
0         NaN  Amazônia   POINT (-9.117 -67.48)  
1         NaN  Amazônia  POINT (-9.055 -67.513)  
2         NaN  Amazônia  POINT (-8.957 -64.141)  
3         NaN  Amazônia  POINT (-8.867 -68.768)  
4         NaN  Amazônia  POINT (-10.62 -69.001)

In [11]:
def replace(match):
    data = {"á": "a", "ã" : "a", "Á": "A","Ã" : "A", "ç": "c", "ê": "e", "Ô":"O"}
    return data.get(match.group(0))

In [12]:
titulo = 'Queimadas - '+ lista[0][idx][0] 

map = fo.Map(location=[-23.5489, -46.6388], 
             title= titulo,
             zoom_start=5,
             width=900, 
             height=1200)
po = fo.FeatureGroup(name='Queimadas')

for row in range(len(df)):
    po.add_child(fo.Marker(location=[ df['latitude'][row], df['longitude'][row]],
                           popup=[re.sub(u'[^a-zA-Z0-9: ]', replace, df['municipio'][row]),
                                  re.sub(u'[^a-zA-Z0-9: ]', replace, df['estado'][row])],
                           icon=fo.Icon(color='red')))    
map.add_child(po)    